In [21]:
import torch
import os
os.environ["KMP_DUPLICATE_LIB_OK"] = "TRUE" # must be used to stop kernel from dying

import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt

from matplotlib.patches import Patch

# Step 1: Load the CSV file
file_path = 'encoding_8oct_(2).csv'  # Replace with your actual file path
df = pd.read_csv(file_path)

# Step 2: Extract nodes, edges, and sarcasm scores
source_ids = df['source_id'].tolist()
target_ids = df['target_id'].tolist()
sarcasm_scores = df['sarcasm_score'].tolist()
sentiment_scores = df['sentiment_score'].tolist()

# Step 3: Calculate percentages for sarcastic vs. non-sarcastic
total_comments = len(sarcasm_scores)
sarcastic_count = sum(1 for score in sarcasm_scores if score == 1)
non_sarcastic_count = total_comments - sarcastic_count

sarcastic_percentage = (sarcastic_count / total_comments) * 100
non_sarcastic_percentage = (non_sarcastic_count / total_comments) * 100

# Step 4: Calculate percentages for sentiment categories
positive_count = sum(1 for score in sentiment_scores if score == 1)
negative_count = sum(1 for score in sentiment_scores if score == 2)
neutral_count = sum(1 for score in sentiment_scores if score == 0)

positive_percentage = (positive_count / total_comments) * 100
negative_percentage = (negative_count / total_comments) * 100
neutral_percentage = (neutral_count / total_comments) * 100

# Step 5: Display the calculated percentages
print(f"Total comments: {total_comments}")
print(f"Sarcastic: {sarcastic_count} ({sarcastic_percentage:.2f}%)")
print(f"Non-sarcastic: {non_sarcastic_count} ({non_sarcastic_percentage:.2f}%)")
print(f"Positive: {positive_count} ({positive_percentage:.2f}%)")
print(f"Negative: {negative_count} ({negative_percentage:.2f}%)")
print(f"Neutral: {neutral_count} ({neutral_percentage:.2f}%)")

# Create a list of edges (source, target)
edges = list(zip(source_ids, target_ids))

# Step 3: Create tensors for the nodes and edges
source_tensor = torch.tensor(source_ids)
target_tensor = torch.tensor(target_ids)

# Step 4: Plot the graph using networkx and matplotlib
G = nx.DiGraph()  # DiGraph() is for directed graphs

# Add edges to the graph
G.add_edges_from(edges)

# Step 5: Extract unique nodes and assign colors based on sarcasm_score
unique_nodes = list(set(source_ids + target_ids))  # Get all unique nodes from sources and targets

node_color_map = {
    node: 'lightgreen' if sentiment_scores[i] == 1 and sarcasm_scores[i] == 0 
          else 'green' if sentiment_scores[i] == 1 and sarcasm_scores[i] == 1 
          else 'pink' if sentiment_scores[i] == 2 and sarcasm_scores[i] == 0 
          else 'red' if sentiment_scores[i] == 2 and sarcasm_scores[i] == 1
          else 'lightblue' if sentiment_scores[i] == 0 and sarcasm_scores[i] == 0
          else 'blue' if sentiment_scores[i] == 0 and sarcasm_scores[i] == 1
          else 'yellow'  # Optional: add a default color if none of the conditions are met
    for i, node in enumerate(source_ids)
}

# Assign a default color for nodes that aren't in the source_ids list (e.g., for isolated nodes)
node_colors = [node_color_map.get(node, 'yellow') for node in unique_nodes]

# Step 10: Create custom legend handles
legend_elements = [
    Patch(facecolor='lightgreen', edgecolor='black', label='Positive, Non-sarcastic'),
    Patch(facecolor='darkgreen', edgecolor='black', label='Positive, Sarcastic'),
    Patch(facecolor='pink', edgecolor='black', label='Negative, Non-sarcastic'),
    Patch(facecolor='red', edgecolor='black', label='Negative, Sarcastic'),
    Patch(facecolor='lightblue', edgecolor='black', label='Neutral, Non-sarcastic'),
    Patch(facecolor='blue', edgecolor='black', label='Neutral, Sarcastic'),
    Patch(facecolor='yellow', edgecolor='black', label='Reddit Topic Node')
]

# Create a labels dictionary with integer formatting
labels = {node: str(int(node)) if pd.notna(node) else 'NaN' for node in unique_nodes}

# Step 6: Plot the graph
plt.figure(figsize=(100, 80))
# Use node_color with the assigned colors
nx.draw(
    G,
    with_labels=True,
    labels=labels, # Pass the labels dictionary here
    nodelist=unique_nodes,
    node_color=node_colors,
    font_weight='bold',
    node_size=3000,
    arrowstyle='->',
    arrowsize=20
)

plt.suptitle('Directed Graph of Reddit Comments and Replies with Sarcasm & Sentiment Score Coloring', fontsize=140)
plt.legend(handles=legend_elements, loc='lower right', title='Node Colors', fontsize=80, title_fontsize=100)
plt.show()

Total comments: 1396
Sarcastic: 172 (12.32%)
Non-sarcastic: 1224 (87.68%)
Positive: 169 (12.11%)
Negative: 679 (48.64%)
Neutral: 548 (39.26%)
